In [ ]:
import pandas as pd
import numpy as np
import re
import os
from unicodedata import normalize
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
folder = '/content/drive/path'
loc = folder + '/TJSP/Raspagem/raspagens-arquivos/[2024-04] arquivos_finais'

In [ ]:
lista=[]
todos = pd.read_excel(folder+ "/termos_utilizados.xlsx")
t_total = todos['termo']
for t in t_total:
  if os.path.exists(loc+"/com-acordaos-"+t+".csv"):
    lista.append(t)

In [ ]:
def retira_termos():
  #retirando termos
  acordaos=acordaos_originais
  for i in range (0, len(acordaos)): #para cada acordao
    for j in termos:
      acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)

    #identifica e retira o nome do relator
    relator = df['relator'][i]
    if (relator in str(acordaos[i])):
      acordaos[i] = acordaos[i].replace(relator, "")

    #identifica e retira o nome do relator, se estiver em letra maiuscula
    relator1 = relator.upper()
    if (relator1 in str(acordaos[i])):
      acordaos[i] = acordaos[i].replace(relator1, "")

In [ ]:
def formatar_ocorrencias(paragrafos):
    ocorrencias_formatadas = []
    for idx, paragrafo in enumerate(paragrafos, start=1):
        ocorrencia = f'ocorrencia {idx}: {paragrafo[1:]}'.replace("\n", " ")
        ocorrencias_formatadas.append(ocorrencia)
    return "\n\n".join(ocorrencias_formatadas)

def busca_ocorrencias(padrao, texto):
        ocorrencias = re.findall(r'[.]?[\w\s\d\,\-\:\–\nº\(\)]*' + padrao + r'[\s\S]*?[.]', texto, re.IGNORECASE)
        return formatar_ocorrencias(ocorrencias)

In [ ]:
termos=['TRIBUNAL.+JUSTI.A.+PAULO','TRIBUNAL.+JUSTI.A','PODER\sJ.+O','AS.+ELETR.NICA','ac.rd.o\n','\s\srelator(a)\n','\s\s\srelator\n','apel.+\s.+\d','reg.+\d','voto.+\d','decl.+\d','s.o.+\sde\s.+\sde\s20[0-2][0-5]','c.mara\n','c.mara:','.*c.mara.+justi.a\n','.*c.mara.+paulo\n','fl.*\d','\n..\n','\n.\n','\n\s*\n','\s\B']

In [ ]:
def busca_mencoes(i, num):
    num = str(num)
    n_processo0 = num

    n_processo1 = re.sub(r"(\d{7})(\d{2})(\d{4})(\d{1})(\d{2})(\d{4})", r"\1-\2.\3.\4.\5.\6", num)

    m = ""

    for l in range(len(acordaos)):
        if processo[l] != processo[i] and n_processo1 in acordaos[l]:
            acordaos[l] = acordaos[l].replace(n_processo1, n_processo0, 1)
            t = str(busca_ocorrencias(n_processo0, l, '.'))
            m += f"PROCESSO: {processo[l]}\nASSUNTO: {assunto[l]}\nTRECHOS: \n{t}\n\n"

    return m

In [ ]:
#para cada termo do resultado
for z in lista:

  caminho = "/content/drive/Shareddrives/Inteligência Artificial: Regulação Jurídica e Políticas Públicas/etapa_1/TJSP/Raspagem/raspagens-arquivos/[2024-04] arquivos_finais/com-acordaos-"+z+".csv"
  df = pd.read_csv(caminho)
  print("iniciando", z,"...")
  if(df.columns[0]!="classe"):
    df = df.drop(df.columns[0], axis=1)

  if(df.columns[9]!="acordao"):
    print("ERRO NA COLUNA DE ACORDAOS. pulando termo....")
    continue

  #cria vetores
  acordaos = df['acordao']
  acordaos_originais = df['acordao']
  processo = df['processo']
  assunto = df['assunto']

  #faz limpeza
  retira_termos()

  #procura ocorrencias do termo nos acordaos
  coluna_trechos = []
  for i in range (0, len(acordaos)):
    coluna_trechos.insert(i, busca_ocorrencias(z,i))

  #procura mencoes de acordaos em outros acordaos
  coluna_mencoes = []
  for i in range (0, len(acordaos)):
    coluna_mencoes.insert(i, busca_mencoes(i,processo[i]))

  #atualiza colunas
  tabela = {'classe': df['classe'],
          'assunto': df['assunto'],
          'relator': df['relator'],
          'comarca': df['comarca'],
          'orgao_julgador': df['orgao_julgador'],
          'data_julgamento':df['data_julgamento'],
          'data_publicacao':df['data_publicacao'],
          'processo': df['processo'],
          'idacordao': df['idacordao'],
          'acordao': acordaos,
          'trechos': coluna_trechos,
          'mencoes': coluna_mencoes,}


  #salva no drive
  final = pd.DataFrame(tabela)
  (final.sort_values(by='relator')).to_csv(caminho,index = False)


iniciando agente de ia ...


<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE

agente de ia ok
iniciando agentes de aprendizado ...
agentes de aprendizado ok


<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE

iniciando agentes moveis ...
agentes moveis ok


...

A saída de streaming foi truncada nas últimas 5000 linhas.
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acorda

sistemas autonomos ok
iniciando sistemas especialistas ...


<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE

sistemas especialistas ok
iniciando visao computacional ...
visao computacional ok


<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE)
<ipython-input-5-aa4d14c032c6>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acordaos[i] = re.sub(j,'',str(acordaos[i]), flags = re.IGNORECASE